In [15]:
import pandas as pd
from tqdm import tqdm
from nltk.stem import PorterStemmer
import text_hammer as th
from nltk.corpus import stopwords
import re
import math

df  = pd.read_csv("dataset.csv")
gps = df[df.label == 'gpsv'].copy()
es = df[df.label == 'esv'].copy()

In [19]:
stop_words = set(stopwords.words("english"))
tqdm.pandas()
ps = PorterStemmer()

def remove_stopwords(text):
    try:
        return " ".join([word for word in text.split() if word not in stop_words])
    except AttributeError:
        print(text)

def text_preprocessing(df,col_name):
    column = col_name
    df[column] = df[column].progress_apply(lambda x: x.lower())
    #df[column] = df[column].progress_apply(lambda x: th.cont_exp(x)) #you're -> you are; i'm -> i am
    df[column] = df[column].progress_apply(lambda x: remove_stopwords(x))
    #df[column] = df[column].progress_apply(lambda x: th.remove_common_words(x, ['allow']))#, 'user', 'allow', 'service', 'version', 'file', 'attacker', 'arbitrary', 'cause', 'execute', 'denial']))
    df[column] = df[column].progress_apply(lambda x: ps.stem(x))
    #df[column] = df[column].progress_apply(lambda x: lemmatizing(x))
    df[column] = df[column].progress_apply(lambda x: th.remove_special_chars(x))
    
    #df[column] = df[column].progress_apply(lambda x: th.make_base(x)) #ran -> run,
    #df[column] = df[column].progress_apply(lambda x: re.sub(r'[^\w\s//-]', '', x))
    return(df)

In [20]:
es_prep = text_preprocessing(es, "description")
gps_prep = text_preprocessing(gps, "description")

100%|██████████| 31211/31211 [00:00<00:00, 81182.06it/s]


In [25]:
import nltk
### Calculating the word frequency by using nltk
words_list = []
for sentence in es.description:
    words_list.extend(nltk.word_tokenize(sentence))
es_freq_dist = nltk.FreqDist(words_list)
es_freq_dist.most_common(100)
#print(freq_dist.keys())    
words_list = []
for sentence in gps.description:
    words_list.extend(nltk.word_tokenize(sentence))
gps_freq_dist = nltk.FreqDist(words_list)
gps_freq_dist.most_common(100)

[('via', 15876),
 ('vulnerability', 15430),
 ('allows', 14017),
 ('attackers', 13099),
 ('remote', 12959),
 ('windows', 12738),
 ('arbitrary', 8906),
 ('plugin', 8544),
 ('wordpress', 7708),
 ('server', 7539),
 ('code', 7329),
 ('users', 6830),
 ('crafted', 6442),
 ('service', 6233),
 ('execute', 5751),
 ('denial', 5433),
 ('cause', 5318),
 ('file', 5133),
 ('unspecified', 4889),
 ('crosssite', 4738),
 ('user', 4684),
 ('attacker', 4525),
 ('memory', 4480),
 ('prior', 4442),
 ('allow', 4335),
 ('versions', 4321),
 ('vectors', 4297),
 ('microsoft', 4213),
 ('scripting', 4100),
 ('could', 3969),
 ('firefox', 3840),
 ('os', 3736),
 ('access', 3697),
 ('aka', 3426),
 ('chrome', 3385),
 ('google', 3336),
 ('web', 3169),
 ('page', 3138),
 ('x', 3059),
 ('xss', 3043),
 ('apache', 3018),
 ('information', 2958),
 ('corruption', 2956),
 ('sp2', 2935),
 ('adobe', 2927),
 ('html', 2851),
 ('issue', 2779),
 ('function', 2762),
 ('data', 2749),
 ('local', 2692),
 ('properly', 2682),
 ('sp1', 2621),


In [84]:
gps_freq_dist['dlink']

0

In [80]:
freq_sum  = 0
words_tf = {}
for word in es_freq_dist.keys():
    freq_sum += es_freq_dist[word]

freq_sum

460650

In [35]:
categories_word_counts = {
    'esv':es_freq_dist,
    'gps':gps_freq_dist,
}

In [81]:
es.label.value_counts().values[0]

13014

In [48]:
count_value

13014

In [39]:
categories_word_counts = {
    'category1': {'word1': 3, 'word2': 5, 'word3': 2},
    'category2': {'word1': 4, 'word2': 1, 'word3': 3},
    'category3': {'word1': 2, 'word2': 3, 'word3': 4},
}

In [21]:
# Term frequency
def tf(word_freq):
    freq_sum  = 0
    words_tf = {}
    for word in word_freq.keys():
        freq_sum += word_freq[word]
    
    for word in word_freq.keys():
        words_tf[word] = word_freq[word] / freq_sum
    return words_tf

In [22]:
es_tf = tf(es_freq_dist)
gps_tf = tf(gps_freq_dist)

In [32]:
def word_exist(word, text):
    text = text.lower()
    return True if re.search(word, text) else False

succes!


In [ ]:
for word in es_freq_dist.keys():
        for text in df.description:
            if word_exist(word, text):
                total_num_text[word] += 1

In [ ]:
# Inverse-Document frequency
def idf(words_dic, n, df, category):
    words = words_dic.keys()
    occurance_freq = {key: 0 for key in words}
    total_num_text = {key: 0 for key in words}
    words_idf = {}
    for word in words:
        for text in category.description:
            if word_exist(word, text):
                occurance_freq[word] += 1
    for word in words:
        for text in df.description:
            if word_exist(word, text):
                total_num_text[word] += 1
    for word in words:
        words_idf[word] = math.log((occurance_freq[word]*n)/total_num_text[word], 10)

    return words_idf
    

   

In [55]:
import numpy as np
from collections import defaultdict
from math import log, sqrt

def compute_tf(category_word_counts, total_word_count_in_category):
    tf = {}
    for word, count in category_word_counts.items():
        tf[word] = count / total_word_count_in_category
    return tf

def compute_idf(categories_word_counts, total_docs):
    idf = {}
    total_word_occurrences = defaultdict(int)

    for category, word_counts in categories_word_counts.items():
        for word in word_counts:
            total_word_occurrences[word] += word_counts[word]

    for word, total_count in total_word_occurrences.items():
        doc_count_per_category = sum(1 for category in categories_word_counts if word in categories_word_counts[category])
        idf[word] = log((doc_count_per_category * total_docs) / total_count)

    return idf

def normalize_tf_idf(tf_idf, categories):
    norm_tf_idf = defaultdict(dict)
    
    for category in categories:
        norm_factor = sqrt(sum((tf_idf[category][word] ** 2 for word in tf_idf[category])))
        for word in tf_idf[category]:
            norm_tf_idf[category][word] = tf_idf[category][word] / norm_factor
    
    return norm_tf_idf

def compute_n_tf_idf(categories_word_counts, total_docs):
    tf = {}
    idf = compute_idf(categories_word_counts, total_docs)
    tf_idf = defaultdict(dict)
    
    for category, word_counts in categories_word_counts.items():
        total_word_count_in_category = sum(word_counts.values())
        tf[category] = compute_tf(word_counts, total_word_count_in_category)
        
        for word, tf_value in tf[category].items():
            tf_idf[category][word] = tf_value * idf[word]
    
    normalized_tf_idf = normalize_tf_idf(tf_idf, categories_word_counts.keys())
    
    return normalized_tf_idf

# Example usage:
categories_word_counts = {
    'esv':es_freq_dist,
    'gps':gps_freq_dist,
}

total_docs = es.label.value_counts().values[0] + gps.label.value_counts().values[0]

n_tf_idf = compute_n_tf_idf(categories_word_counts, total_docs)
max_n_tf_idf_per_word = defaultdict(float)
for category, word_scores in n_tf_idf.items():
    print(f"Category: {category}")
    for word, score in word_scores.items():
        print(f"  Word: {word}, N-TF-IDF: {score}")

# Iterate over each category's N-TF-IDF values to find the maximum for each word
for category, word_scores in n_tf_idf.items():
    for word, score in word_scores.items():
        # Update the maximum N-TF-IDF value for each word
        max_n_tf_idf_per_word[word] = max(max_n_tf_idf_per_word[word], score)


Category: esv
  Word: memory, N-TF-IDF: 0.06443830800430621
  Word: corruption, N-TF-IDF: 0.026190990036850176
  Word: issue, N-TF-IDF: 0.17449136251277053
  Word: addressed, N-TF-IDF: 0.06656402057117117
  Word: improved, N-TF-IDF: 0.06495269922545728
  Word: handling, N-TF-IDF: 0.030498548070451235
  Word: fixed, N-TF-IDF: 0.0671496865037186
  Word: ios, N-TF-IDF: 0.16615525075454493
  Word: 1331, N-TF-IDF: 0.006004676069544219
  Word: ipados, N-TF-IDF: 0.05484803318616065
  Word: application, N-TF-IDF: 0.13433975291207506
  Word: may, N-TF-IDF: 0.09147256166262752
  Word: able, N-TF-IDF: 0.048214559511257464
  Word: execute, N-TF-IDF: 0.06594379754266198
  Word: arbitrary, N-TF-IDF: 0.07220810653382419
  Word: code, N-TF-IDF: 0.07469869191040428
  Word: kernel, N-TF-IDF: 0.07351726806027506
  Word: privileges, N-TF-IDF: 0.08323702940216628
  Word: outofbounds, N-TF-IDF: 0.019052554074393508
  Word: read, N-TF-IDF: 0.038028262056317645
  Word: input, N-TF-IDF: 0.03604380402268821
  W

In [89]:
max_n_tf_idf_per_word['attackers']

0.16665492610886248

In [87]:
n_tf_idf['esv']['firmware']

0.06172597240385516